In [ ]:
!pip install pyspark py4j

In [ ]:
import tarfile
import pandas as pd
from google.colab import files
from google.colab import drive
import matplotlib.pyplot as plt
# plt.style.use("seaborn-deep")
import seaborn as sns
import csv
%matplotlib inline
#Spark
from pyspark.sql.functions import *
import pyspark.pandas as ps
import datetime

In [ ]:
drive.mount('/content/drive')

In [ ]:
! mkdir ~/.kaggle
! cp kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json
! kaggle datasets download -d yelp-dataset/yelp-dataset
! mkdir data
! unzip yelp-dataset.zip -d data

100% 4.06G/4.07G [00:56<00:00, 65.3MB/s]
100% 4.07G/4.07G [00:56<00:00, 77.8MB/s]
Archive:  yelp-dataset.zip
  inflating: data/Dataset_User_Agreement.pdf  
  inflating: data/yelp_academic_dataset_business.json  
  inflating: data/yelp_academic_dataset_checkin.json  
  inflating: data/yelp_academic_dataset_review.json  
  inflating: data/yelp_academic_dataset_tip.json  
  inflating: data/yelp_academic_dataset_user.json  


In [ ]:
from pyspark.sql import SparkSession
spark = SparkSession.builder\
    .master('local[*]') \
    .config("spark.driver.memory", "10g")\
  .appName("taller2_eda").getOrCreate()

In [ ]:
business_df = spark.read.json('./data/yelp_academic_dataset_business.json')
user_df = spark.read.parquet('/content/drive/MyDrive/uniandes/mine/sr/taller2/user/')
reviews_df = spark.read.parquet('/content/drive/MyDrive/uniandes/mine/sr/taller2/reviews/')
checkin_df = spark.read.json('./data/yelp_academic_dataset_checkin.json')
tip_df = spark.read.json('./data/yelp_academic_dataset_tip.json')

## Negocios

In [ ]:
business_ks_df = ps.DataFrame(business_df)
user_ks_df = ps.DataFrame(user_df)
reviews_ks_df = ps.DataFrame(reviews_df)
checkin_ks_df = ps.DataFrame(checkin_df)
tip_ks_df = ps.DataFrame(tip_df)

In [ ]:
business_ks_df.head()

address                                                                                                                                                                                                                                                                                                                         attributes             business_id                                                                                                  categories           city                                                                   hours  is_open   latitude   longitude                      name postal_code  review_count  stars state
0           1616 Chapala St, Ste 2                                                                                         (None, None, None, None, None, None, None, None, None, None, None, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None)  Pns2l4eNsfO8kk83dixA6A  Doctors, Traditional Chinese Medicine, Naturopathic/Holistic, Acupuncture, Health & Medical, Nutritionists  Santa Barbara                                                                    None        0  34.426679 -119.711197  Abby Rappoport, LAC, CMQ       93101             7    5.0    CA
1  87 Grasso Plaza Shopping Center                                                                                         (None, None, None, None, None, None, None, None, None, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None)  mpf3x-BjTdTEA3yCZrAYPw                              Shipping Centers, Local Services, Notaries, Mailbox Centers, Printing Services         Affton   (8:0-18:30, 0:0-0:0, 8:0-14:0, None, 8:0-18:30, 8:0-18:30, 8:0-18:30)        1  38.551126  -90.335695             The UPS Store       63123            15    3.0    MO
2             5255 E Broadway Blvd  (None, None, None, None, None, None, None, True, None, True, {'garage': False, 'street': False, 'validated': False, 'lot': True, 'valet': False}, False, False, False, None, None, False, None, None, None, None, None, False, False, None, None, None, False, None, None, False, None, 2, False, None, False, None, True, u'no')  tUFrWirKiKi_TAnsVWINQQ                          Department Stores, Shopping, Fashion, Home & Garden, Electronics, Furniture Stores         Tucson  (8:0-23:0, 8:0-22:0, 8:0-23:0, 8:0-22:0, 8:0-22:0, 8:0-22:0, 8:0-22:0)        0  32.223236 -110.880452                    Target       85711            22    3.5    AZ
3                      935 Race St   (None, None, u'none', None, None, None, None, True, None, False, {'garage': False, 'street': True, 'validated': False, 'lot': False, 'valet': False}, False, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, False, None, None, False, None, 1, None, None, True, None, None, u'free')  MTSW4McQd7CbVtyjqoe9mw                                                       Restaurants, Food, Bubble Tea, Coffee & Tea, Bakeries   Philadelphia  (7:0-21:0, 7:0-20:0, 7:0-21:0, 7:0-21:0, 7:0-20:0, 7:0-20:0, 7:0-20:0)        1  39.955505  -75.155564        St Honore Pastries       19107            80    4.0    PA
4                    101 Walnut St            (None, None, None, None, None, None, None, True, None, True, {'garage': None, 'street': None, 'validated': None, 'lot': True, 'valet': False}, None, False, None, None, None, None, None, None, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, True, None, True, None)  mWMc6_wTdE0EUBKIGXDVfA                                                                                   Brewpubs, Breweries, Food     Green Lane     (12:0-22:0, None, 12:0-22:0, 12:0-18:0, 16:0-22:0, None, 14:0-22:0)        1  40.338183  -75.471659  Perkiomen Valley Brewery       18054           

In [ ]:
num_business = business_df.count()
print('Número total de negocios: ', num_business)

Número total de negocios:  150346


### Categorías mas populares

In [ ]:
categories_df = business_ks_df.assign(categories=business_ks_df['categories'].str.split(', ')).explode('categories')
categories_df

address                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   attributes             business_id                        categories                 city                                                                                    hours  is_open   latitude   longitude                                               name postal_code  review_count  stars state
0                        1616 Chapala St, Ste 2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   (None, None, None, None, None, None, None, None, None, None, None, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None)  Pns2l4eNsfO8kk83dixA6A                           Doctors        Santa Barbara                                                                                     None        0  34.426679 -119.711197                           Abby Rappoport, LAC, CMQ       93101             7    5.0    CA
0                        1616 Chapala St, Ste 2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   (None, None, None, None, None, None, None, None, None, None, None, True, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None, None)  Pns2l4eNsfO8kk83dixA6A      Traditional Chinese Medicine        Santa Barbara                                                                                     None        0  34.426679 -119.711197                           Abby Rappoport, LAC, CMQ       93101             7    5.0    CA
0                        1616 Chapala St, Ste 2                                                                                                                                                                                                                                                                                                                                                                                                            

Se realiza la gráfica de las 20 categorías más populares

In [ ]:
category_counts = categories_df['categories'].value_counts()
# Select the top 20 categories
top_categories = category_counts.head(20)
top_categories.plot(kind='bar', labels={'index':"Categoría", 'value': 'Cantidad de negocios'}, title="Top categorías de negocios")

In [ ]:
categories_df['categories'].unique()

0                            Dermatologists
1                          Historical Tours
2                            Paddleboarding
3                          Hot Air Balloons
4                       Mobile Home Dealers
5                                   Beaches
6                           Pet Photography
7                             Skating Rinks
8                             Data Recovery
9                              Aerial Tours
10                              Boat Repair
11                                   Fondue
12                            Videographers
13                        Pet Waste Removal
14     Faith-based Crisis Pregnancy Centers
15                             Contract Law
16                              Hobby Shops
17                                 Day Spas
18                                 Honduran
19                                    Reiki
20                            Nephrologists
21                      Private Jet Charter
22                              

In [ ]:
len(business_ks_df)

150346

En el conjunto de datos hay en total 150346 negocios.

In [ ]:
len(business_ks_df[business_ks_df['categories'].str.contains('Restaurants')])

52268

Del total de negocios, 52268 están asociados a la categoría restaurantes.

In [ ]:
len(reviews_ks_df)

6990280

En el conjunto total de datos hay 6990280 calificaciones.

In [ ]:
restaurant_business_ks_df = business_ks_df[business_ks_df['categories'].str.contains('Restaurants')]
len(restaurant_business_ks_df.merge(reviews_ks_df, how='inner', on='business_id'))

4724471

Del total de calificaciones hay 4724471 asociadas a los negocios de categoría restaurantes.

### Top 20 ciudades con mayor cantidad de negocios en el dataset

In [ ]:
city_business_ks_df = business_ks_df['city'].value_counts()
# Select the top 20 cities
city_business_ks_df=city_business_ks_df.sort_values(ascending=False)
top_cities = city_business_ks_df.head(20)
top_cities.plot(kind='bar', labels={'index':"Ciudad", 'value': 'Cantidad de negocios'}, title="Top ciudades con mayor cantidad de negocios")


De la gráfica anterior observamos que

In [ ]:
states_business_ks_df = business_ks_df['state'].value_counts()
# Select the top 60 cities
top_states= states_business_ks_df.head(60)
top_states.plot(kind='bar', labels={'index':"Estado", 'value': 'Cantidad de negocios'}, title="Top estados de EE.UU. con mayor cantidad de negocios")

### Calificaciones

In [ ]:
business_ks_df['stars'].value_counts().sort_index().plot(kind='bar', labels={'index':"Estrellas", 'value': 'Cantidad de negocios'}, title="Distribución de las calificaciones entre los negocios")

### Variable is_open

In [ ]:
business_ks_df['is_open'].value_counts().sort_index().plot(kind='bar', labels={'index':"is_open", 'value': 'Cantidad de negocios'}, title="Distribución de las variable is_open entre los negocios")

In [ ]:
business_ks_df['is_open'].value_counts().sort_index().plot(kind='bar', labels={'index':"is_open", 'value': 'Cantidad de negocios'}, title="Distribución de las variable is_open entre los negocios")

### Variable review_count

In [ ]:
business_ks_df['review_count'].value_counts().sort_index().plot(kind='hist', hue=True, bins= 20,
                                                                labels={'index':"Conteo calificaciones", 'count': 'Cantidad de negocios'}, title="Distribución de la variable review_count entre los negocios")

## Usuarios

In [ ]:
user_ks_df.head()

average_stars  compliment_cool  compliment_cute  compliment_funny  compliment_hot  compliment_list  compliment_more  compliment_note  compliment_photos  compliment_plain  compliment_profile  compliment_writer  cool                                                         elite  fans                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [ ]:
num_users = user_df.count()
print('Número total de usuarios: ', num_users)

Número total de usuarios:  1987897


In [ ]:
# Count the number of reviews, fans, and friends for each user
user_agg = user_df.agg(
    sum('review_count').alias('total_reviews'),
    sum('fans').alias('total_fans'),
    sum(size(split('friends', ', '))).alias('total_friends')
).collect()

In [ ]:
# Print the aggregate results
print('Total reviews:', user_agg[0]['total_reviews'])
print('Total fans:', user_agg[0]['total_fans'])
print('Total friends:', user_agg[0]['total_friends'])

Total reviews: 46505676
Total fans: 2913741
Total friends: 106104025


In [ ]:
user_ks_df['years_on_yelp'].plot(kind='hist', labels={'value':"Años en Yelp", 'count': 'Cantidad de usuarios'}, title="Distribución de la antiguedad de los usuarios")

In [ ]:
user_ks_df['yelping_since'] = user_ks_df['yelping_since'].astype(str).apply(lambda x : x[:4]).astype(int)
now = datetime.datetime.now().year
user_ks_df['years_on_yelp'] = (now - user_ks_df['yelping_since'])

In [ ]:
user_ks_df['years_on_yelp'].plot(kind='hist', labels={'value':"Años en Yelp", 'count': 'Cantidad de usuarios'}, title="Distribución de la antiguedad de los usuarios")

In [ ]:
user_ks_df['average_stars'].plot(kind='hist', labels={'value':"average_stars", 'count': 'Cantidad de usuarios'}, title="Distribución de las variable average_stars entre los usuarios")

In [ ]:
user_ks_df['fans'].plot(kind='hist', labels={'index':"fans", 'value': 'Count'}, title="Distribución de las variable fans entre los usuarios")

In [ ]:
user_ks_df['useful'].plot(kind='hist', labels={'index':"useful", 'value': 'Count'}, title="Distribución de las variable useful entre los usuarios")

In [ ]:
user_ks_df['review_count'].plot(kind='hist', bins=30, labels={'index':"review_count", 'value': 'Count'}, title="Distribución de las variable review_count entre los usuarios")

## Calificaciones

In [ ]:
reviews_ks_df.head()

business_id  cool                 date  funny               review_id  stars                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           text  useful                 user_id
0  3ZynJ94VpIdDlaArmEp2Rg     0  2013-10-03 16:24:30      0  RGV9GWhAAfAAlYyd4vho7g    3.0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           A couple friends and I stopped by for some late night milkshakes and found ourselves at More Than Just Ice Cream. Well, we just got ice cream...not fully taking advantage of what the name implies, but maybe next time.\n\n3 milkshakes: 1 coffee, 1 chocolate, and 1 black&white malt. \n\nAll were pretty good. Definitely satisfied the ice cream craving. I thought my coffee milkshake could have been thicker, same goes for the chocolate. The black&white was plenty thick and was probably the best of the three. Unfortunately, I did not order that one so I settled for my not so creamy coffee.\n\nI did sample some ice cream flavors before setting on a milkshake. I tried the pumpkin pie which was AMAZING. I don't know why I didn't just get this. Maybe a milkshake isn't the way to go here.       0  Zs8Zk3sgh5JxRmoZW4PJcg
1  b7V_5q22_eTeHlYzq1bpFw     0  2017-01-02 04:12:17      

In [ ]:
num_reviews = reviews_ks_df.count()
print('Número total de reviews: ', num_reviews)

Número total de reviews:  business_id    6990280
cool           6990280
date           6990280
funny          6990280
review_id      6990280
stars          6990280
text           6990280
useful         6990280
user_id        6990280
dtype: int64


In [ ]:
reviews_ks_df['stars'].value_counts().plot(kind='bar', labels={'index':"Estrellas", 'value': 'Cantidad de calificaciones'}, title="Distribución de las variable stars entre las calificaciones")

In [ ]:
reviews_ks_df['cool'].value_counts().plot(kind='hist', labels={'index':"cool", 'value': 'Cantidad de calificaciones'}, title="Distribución de las variable cool entre las calificaciones")

In [ ]:
reviews_ks_df['useful'].value_counts().plot(kind='hist', labels={'value':"useful", 'value': 'Count'}, title="Distribución de las variable useful entre las calificaciones")

In [ ]:
reviews_ks_df.merge(user_ks_df[['user_id', 'name']], on='user_id', how='left')

business_id  cool                 date  funny               review_id  stars                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [ ]:
reviews_ks_df.groupby('user_id').count().reset_index().merge(user_ks_df[['user_id', 'name']], on='user_id', how='left').sort_values('business_id', ascending=False)[['business_id','name']]

business_id                 name
1539048         3048                Karen
327165          1840             Marielle
609000          1747                  Jen
599291          1682               Gerald
740747          1653             Michelle
964011          1578               Steven
21338           1554              Shannon
1925148         1447                 Boon
1159825         1396                  Ken
1887516         1391               Dianna
1105711         1324               Rachel
1493897         1308                 Mark
961760          1298                 Bill
502542          1247                Brett
1088812         1129                Danan
112699          1087                Allie
6985            1076            Christina
1744328         1071              Michael
724110          1047          Christopher
701848          1041             Brittany
1847751         1023                Kathy
502681           978                Steve
1300621          964                Steve
1784051          954                Wanda
845765           947             Michelle
34664            938                Peter
1897368          927                    P
397128           922                 Patt
1057481          917          Christopher
556975           900             michelle
73693            888                 Dave
459554           866              Kristin
14506            863                 Phil
165170           860             Kathleen
181055           844                Erica
1746691          834                 Nick
514138           830                Paula
1016334          829               Alexis
1508937          829                 Niki
1428498          823               Nicole
69197            820             Isabella
1028329          790                Kelly
141416           780              Charles
1646460          773                  Ali
1748953          772                James
157057           770              Mallory
1783579          767               Tricia
1124087          764             Virginia
1296553          758              Richard
1652060          744              Christy
382533           742                 John
1428948          733             Michelle
1674619          732               Carlos
1641144          729             Kelleigh
873891           725             Brigitte
858863           719                Craig
553021           714                Retna
682822           698                 Jeff
271083           687                 Mike
835683           675               Steven
1357309          671               Robert
657685           666               Marcia
858405           664               Amy OO
1299128          662                  Les
1802047          661         Sari Marissa
1535306          660                 Dave
419896           659                  Bob
790620           658                 Dana
1503714          658                Jenny
5214             657               DeAnna
970972           647                  Jay
1507029          647                Karen
791455           644               Ameesh
47975            641            Stephanie
11818            640                  Joi
213285           638               Robert
140170           637                Donna
434313           633              John L.
1227671          628               Mandie
823117           622                 Brad
1414361          619                 Todd
983909           617                 Alex
1488551          617                Aimee
11405            611              Abraham
1582379          606                  Dee
1257769          604                Sarah
1225261          602               Sheena
707497           598               Teneha
12728            597                 Jenn
1757219          596               Violet
1353479          593                Mandy
662278           590              Michael
1241457          589              Allison
590011           587                David
317568           58

In [ ]:
reviews_ks_df.groupby('user_id').count().sort_values('business_id', ascending=False)['business_id'].head(20)

user_id
_BcWyKQL16ndpBdggh2kNA    3048
Xw7ZjaGfr0WNVt6s_5KZfA    1840
0Igx-a1wAstiBDerGxXk2A    1747
-G7Zkl1wIWBBmD0KRy_sCw    1682
ET8n-r7glWYqZhuR6GcdNw    1653
bYENop4BuQepBjM1-BI3fA    1578
1HM81n6n4iPIFU5d2Lokhw    1554
fr1Hz2acAb3OaL3l6DyKNg    1447
wXdbkFZsfDR7utJvbWElyA    1396
Um5bfs5DH6eizgjH3xZsvg    1391
qjfMBIZpQT9DDtw_BWCopQ    1324
VL12EhEdT4OWqGq0nIqkzw    1308
bJ5FtCtZX3ZZacz2_2PJjA    1298
pou3BbKsIozfH50rxmnMew    1247
ouODopBKF3AqfCkuQEnrDg    1129
B-s-8VUnuBjGTP3d01jsyw    1087
-kLVfaJytOJY2-QdQoCcNQ    1076
vHc-UrI9yfL_pnnc6nJtyQ    1071
CfX4sTIFFNaRchNswqhVfg    1047
AHRrG3T1gJpHvtpZ-K0G_g    1041
Name: business_id, dtype: int64

In [ ]:
max_reviews_users = reviews_ks_df.groupby('user_id').count().reset_index().merge(user_ks_df[['user_id', 'name']], on='user_id', how='left').sort_values('business_id', ascending=False)[['business_id','name']]
ps.Series(data=max_reviews_users, index=max_reviews_users['business_id'])

In [ ]:
max_reviews_users.set_index('business_id')['name'].head(20)

name
business_id             
3048               Karen
1840            Marielle
1747                 Jen
1682              Gerald
1653            Michelle
1578              Steven
1554             Shannon
1447                Boon
1396                 Ken
1391              Dianna
1324              Rachel
1308                Mark
1298                Bill
1247               Brett
1129               Danan
1087               Allie
1076           Christina
1071             Michael
1047         Christopher
1041            Brittany

In [ ]:
max_reviews_users.set_index('name').head(20)\
.plot(kind='bar', labels={'user_id':"Usuarios", 'value': 'Cantidad de calificaciones'}, title="Usuarios con mas calificaciones")

Negocio con mejores calificaciones

In [ ]:
business_avg_stars = reviews_ks_df.groupby('business_id')['stars'].mean()

Restaurantes con mejor promedio de calificaciones:

In [ ]:
restaurant_business_ks_df[['business_id', 'name']].merge(business_avg_stars.reset_index(), on='business_id', how='inner').sort_values(by='stars', ascending=False).head(40)\
[['name', 'stars']]

name  stars
1232              Crown Chicken & Gyro    5.0
1261                      Taco Station    5.0
1585                  Big Green Bistro    5.0
1725      El Guero  Mexican Food Truck    5.0
2355                   Belle Fouchette    5.0
2716                          Mintwist    5.0
3681                     Wayne Lee, MD    5.0
4348                   The Sweet Coquí    5.0
4654            Beans BBQ and Catering    5.0
5077                   George's Corner    5.0
5341                     Papa Murphy's    5.0
5593                  Groark Boys’ BBQ    5.0
5679    Philadelphia Soft Pretzels Inc    5.0
5775                    Polka Deli Inc    5.0
6609            One Up One Down Coffee    5.0
6617                    Kensington Pub    5.0
7700                   Arbuckle Coffee    5.0
7974                          Il Forno    5.0
8244            La Michoacana Deluxe 2    5.0
8294           Happy Ending Food Truck    5.0
8312         Annie Moons Bakery & Cafe    5.0
8346             Himes Breakfast House    5.0
8431                      Urban Crudos    5.0
8542                 GI Juice and Java    5.0
8853                  AJ’s Jazzy Grill    5.0
8873          Gonzo's Smokehouse & BBQ    5.0
9123                     Labadee house    5.0
9155           Sabroso Cocina Mexicana    5.0
9475   Brew Garden Taphouse and Eatery    5.0
9506                    Brown Dog Cafe    5.0
9573            Golden Line Coffee Bar    5.0
9728                       Scoop Shack    5.0
9827                      WUDON K BOWL    5.0
10061                  The Pepper Pott    5.0
10072                        Sab Sushi    5.0
10179             Charly's BBQ & Grill    5.0
10189            Tacos el Velvet Elvis    5.0
10210                 Peter James BYOB    5.0
10217          Sweet Southern Heat BBQ    5.0
10372                    Gino's Bakery    5.0

## Checkins

In [ ]:
checkin_ks_df.head()

business_id                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              date
0  ---kPU91CF4Lq2-WlRu9Lw                                                                                                                                                                                                                                                                                                                             2020-03-13 21:10:56, 2020-06-02 22:18:06, 2020-07-24 22:42:27, 2020-10-24 21:36:13, 2020-12-09 21:23:33, 2021-01-20 17:34:57, 2021-04-30 21:02:03, 2021-05-25 21:16:54, 2021-08-06 21:08:08, 2021-10-02 15:15:42, 2021-11-11 16:23:50
1  --0iUa4sNDFiZFrAdIWhZQ                                                                                                                                                                                                                                                                                                                                                  2010-09-13 21:43:09, 2011-05-04 23:08:15, 2011-07-18 22:30:31, 2012-09-07 20:28:50, 2013-03-27 15:57:36, 2013-08-13 00:31:34, 2013-08-13 00:31:48, 2013-09-23 17:39:38, 2013-11-18 06:34:08, 2014-04-12 23:04:47
2  --30_8IhuyMHbSOcNWd6DQ                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          2013-06-14 23:29:17, 2014-08-13 23:20:22
3  --7PUidqRWpRSpXebiyxTg                                                                                                                                                                                                                                                                                                                                                  2011-02-15 17:12:00, 2011-07-28 02:46:10, 2012-03-11 10:30:02, 2012-04-24 07:07:59, 2012-04-24 07:43:31, 2013-05-25 16:41:10, 2014-05-02 15:49:55, 2014-09-18 02:28:23, 2014-11-10 15:16:43, 2015-09-27 13:18:32
4  --7jw19RH9JKXgFohspgQw  2014-04-21 20:42:11, 2014-04-28 21:04:46, 2014-09-30 14:41:47, 2014-10-23 18:22:28, 2015-04-27 19:55:00, 2015-09-21 12:52:09, 2015-10-01 12:46:16, 2015-10-22 13:35:04, 2016-01-14 12:27:43, 2016-02-01 15:15:07, 2016-02-11 12:22:47, 2016-03-31 23:15:46, 2016-04-11 13:11:34, 2016-05-25 12:44:11, 2016-06-27 15:46:11, 2016-06-30 15:14:28, 2016-07-28 14:15:59, 2016-09-22 20:05:06, 2016-11-16 19:00:11, 2016-12-27 14:36:14, 2017-01-24 20:18:16, 2017-02-21 16:01:49, 2017-03-21 14:08:44, 2017-05-21 16:07:21, 2017-08-07 14:17:39, 2021-06-21 19:59:50

In [ ]:
num_checkin = checkin_df.count()
print('Número total de checkin: ', num_checkin)

Número total de checkin:  131930


## Tip

In [ ]:
tip_ks_df.head()

business_id  compliment_count                 date                                                       text                 user_id
0  3uLgwr0qeCNMjKenHJwPGQ                 0  2012-05-18 02:17:21                             Avengers time with the ladies.  AGNUgVwnZUey3gcPCJ76iw
1  QoezRbYQncpRqyrLH6Iqjg                 0  2013-02-05 18:35:10  They have lots of good deserts and tasty cuban sandwiches  NBN4MgHP9D3cw--SnauTkA
2  MYoRNLb5chwjQe3c_k37Gg                 0  2013-08-18 00:56:08                     It's open even when you think it isn't  -copOvldyKh1qr-vzkDEvw
3  hV-bABTK-glh5wj31ps_Jw                 0  2017-06-27 23:05:38                                  Very decent fried chicken  FjMQVZjSqY8syIO-53KFKw
4  _uN0OudeJ3Zl_tf6nxg5ww                 0  2012-10-06 19:43:09                     Appetizers.. platter special for lunch  ld0AperBXk1h6UbqmM80zw

In [ ]:
num_tips = tip_df.count()
print('Número total de tip: ', num_tips)

Número total de tip:  908915


In [ ]:
tip_ks_df['compliment_count'].value_counts()\
.plot(kind='bar', labels={'index':"Cantidad compliments", 'value': 'Cantidad'}, title="Distribución de las variable compliment entre las propinas")

Restaurante con más propinas

In [ ]:
restaurant_business_ks_df.merge(tip_ks_df, on='business_id', how='left').groupby(['business_id', 'name']).count()['address'].reset_index().sort_values(by='address', ascending=False)\
[['name',	'address']].head(20)

name  address
29192                       Café Du Monde     2571
20602                   Acme Oyster House      932
25634             Reading Terminal Market      827
20791                        Oceana Grill      613
29377                                Luke      608
9429                  Mother's Restaurant      606
16512  Hattie B’s Hot Chicken - Nashville      579
3972                   Pappy's Smokehouse      577
5522                                 Datz      551
49723          Ruby Slipper - New Orleans      541
48055                      Cochon Butcher      532
25545                          Los Agaves      526
32392                         Royal House      512
31591      Dalessandro’s Steaks & Hoagies      460
45484     Felix's Restaurant & Oyster Bar      441
27456                              Cochon      439
27439                       Pat O'Brien’s      426
33361                  Commander's Palace      406
5357                 Pat's King of Steaks      400
16129                             Stanley      389

In [ ]:
restaurant_business_ks_df.merge(tip_ks_df, on='business_id', how='left').groupby(['business_id', 'name']).count()['address'].reset_index().sort_values(by='address', ascending=False)\
[['name',	'address']].head(20).set_index('name')\
.plot(kind='bar', labels={'index':"Restaurante", 'value': 'Cantidad'}, title="Restaurantes con mas propinas")